<a href="https://colab.research.google.com/github/mvsakrishna/Assignment/blob/main/Mousai.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!git clone https://github.com/archinetai/audio-diffusion-pytorch.git

Cloning into 'audio-diffusion-pytorch'...
remote: Enumerating objects: 958, done.
remote: Counting objects: 100% (181/181), done.
remote: Compressing objects: 100% (76/76), done.
remote: Total 958 (delta 165), reused 113 (delta 104), pack-reused 777
Receiving objects: 100% (958/958), 258.50 KiB | 6.15 MiB/s, done.
Resolving deltas: 100% (660/660), done.


In [2]:
%cd audio-diffusion-pytorch

/content/audio-diffusion-pytorch


In [3]:
!pip install audio-diffusion-pytorch

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.7/42.7 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 3.6 MB/s eta 0:00:00


In [4]:
!pip install torchvision


## Uncnditional Audio music

In [5]:
from audio_diffusion_pytorch import DiffusionModel, UNetV0, VDiffusion, VSampler
import torch

model = DiffusionModel(
    net_t=UNetV0, # The model type used for diffusion (U-Net V0 in this case)
    in_channels=2, # U-Net: number of input/output (audio) channels
    channels=[8, 32, 64, 128, 256, 512, 512, 1024, 1024], # U-Net: channels at each layer
    factors=[1, 4, 4, 4, 2, 2, 2, 2, 2], # U-Net: downsampling and upsampling factors at each layer
    items=[1, 2, 2, 2, 2, 2, 2, 4, 4], # U-Net: number of repeating items at each layer
    attentions=[0, 0, 0, 0, 0, 1, 1, 1, 1], # U-Net: attention enabled/disabled at each layer
    attention_heads=8, # U-Net: number of attention heads per attention item
    attention_features=64, # U-Net: number of attention features per attention item
    diffusion_t=VDiffusion, # The diffusion method used
    sampler_t=VSampler, # The diffusion sampler used
)

# Train model with audio waveforms
audio = torch.randn(1, 2, 2**18) # [batch_size, in_channels, length]
loss = model(audio)
loss.backward()

# Turn noise into new audio sample with diffusion
noise = torch.randn(1, 2, 2**18) # [batch_size, in_channels, length]
sample = model.sample(noise, num_steps=10) # Suggested num_steps 10-100

In [6]:
sample

tensor([[[-0.0928,  0.1430, -0.0794,  ...,  0.1562, -0.1882,  0.0428],
         [ 0.0988,  0.1531,  0.0461,  ..., -0.0995, -0.2266,  0.2046]]])

In [7]:
sample.shape

torch.Size([1, 2, 262144])

In [8]:
from IPython.display import Audio
import torch

# Assuming your tensor is named 'audio_tensor'
# Convert the tensor to a NumPy array
audio_array = sample.numpy().reshape(-1)

# Specify the sample rate (replace with your actual sample rate)
sample_rate = 44100

# Use the Audio class to play the audio in Colab
Audio(data=audio_array, rate=sample_rate)

# Text Conditional Audio Music

In [9]:
!pip install transformers

In [10]:
from audio_diffusion_pytorch import DiffusionModel, UNetV0, VDiffusion, VSampler

model = DiffusionModel(
    # ... same as unconditional model
    net_t=UNetV0, # The model type used for diffusion (U-Net V0 in this case)
    in_channels=2, # U-Net: number of input/output (audio) channels
    channels=[8, 32, 64, 128, 256, 512, 512, 1024, 1024], # U-Net: channels at each layer
    factors=[1, 4, 4, 4, 2, 2, 2, 2, 2], # U-Net: downsampling and upsampling factors at each layer
    items=[1, 2, 2, 2, 2, 2, 2, 4, 4], # U-Net: number of repeating items at each layer
    attentions=[0, 0, 0, 0, 0, 1, 1, 1, 1], # U-Net: attention enabled/disabled at each layer
    attention_heads=8, # U-Net: number of attention heads per attention item
    attention_features=64, # U-Net: number of attention features per attention item
    diffusion_t=VDiffusion, # The diffusion method used
    sampler_t=VSampler, # The diffusion sampler used
    use_text_conditioning=True, # U-Net: enables text conditioning (default T5-base)
    use_embedding_cfg=True, # U-Net: enables classifier free guidance
    embedding_max_length=64, # U-Net: text embedding maximum length (default for T5-base)
    embedding_features=768, # U-Net: text mbedding features (default for T5-base)
    cross_attentions=[0, 0, 0, 1, 1, 1, 1, 1, 1], # U-Net: cross-attention enabled/disabled at each layer
)

# Train model with audio waveforms
audio_wave = torch.randn(1, 2, 2**18) # [batch, in_channels, length]
loss = model(
    audio_wave,
    text=['Guitar'], # Text conditioning, one element per batch
    embedding_mask_proba=0.1 # Probability of masking text with learned embedding (Classifier-Free Guidance Mask)
)
loss.backward()

# Turn noise into new audio sample with diffusion
noise = torch.randn(1, 2, 2**18)
sample = model.sample(
    noise,
    text=['Guitar'],
    embedding_scale=5.0, # Higher for more text importance, suggested range: 1-15 (Classifier-Free Guidance Scale)
    num_steps=2 # Higher for better quality, suggested num_steps: 10-100
)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/t5/tokenization_t5_fast.py:160: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-base automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  warnings.warn(


model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

In [11]:
sample

tensor([[[-0.0016,  0.0007,  0.0040,  ...,  0.0029,  0.0055,  0.0031],
         [ 0.0165, -0.0074,  0.0045,  ..., -0.0078, -0.0025,  0.0061]]])

In [12]:
from audio_diffusion_pytorch import DiffusionUpsampler, UNetV0, VDiffusion, VSampler

upsampler = DiffusionUpsampler(
    net_t=UNetV0, # The model type used for diffusion
    upsample_factor=16, # The upsample factor (e.g. 16 can be used for 3kHz to 48kHz)
    in_channels=2, # U-Net: number of input/output (audio) channels
    channels=[8, 32, 64, 128, 256, 512, 512, 1024, 1024], # U-Net: channels at each layer
    factors=[1, 4, 4, 4, 2, 2, 2, 2, 2], # U-Net: downsampling and upsampling factors at each layer
    items=[1, 2, 2, 2, 2, 2, 2, 4, 4], # U-Net: number of repeating items at each layer
    diffusion_t=VDiffusion, # The diffusion method used
    sampler_t=VSampler, # The diffusion sampler used
)

# Train model with high sample rate audio waveforms
audio = torch.randn(1, 2, 2**18) # [batch, in_channels, length]
loss = upsampler(audio)
loss.backward()

# Turn low sample rate audio into high sample rate
downsampled_audio = torch.randn(1, 2, 2**14) # [batch, in_channels, length]
sample = upsampler.sample(downsampled_audio, num_steps=10) # Output has shape: [1, 2, 2**18]

In [13]:
from IPython.display import Audio
import torch

# Assuming your tensor is named 'audio_tensor'
# Convert the tensor to a NumPy array
audio_array = sample.numpy().reshape(-1)

# Specify the sample rate (replace with your actual sample rate)
sample_rate = 44100

# Use the Audio class to play the audio in Colab
Audio(data=audio_array, rate=sample_rate)

In [14]:
from audio_diffusion_pytorch import DiffusionVocoder, UNetV0, VDiffusion, VSampler

vocoder = DiffusionVocoder(
    mel_n_fft=1024, # Mel-spectrogram n_fft
    mel_channels=80, # Mel-spectrogram channels
    mel_sample_rate=48000, # Mel-spectrogram sample rate
    mel_normalize_log=True, # Mel-spectrogram log normalization (alternative is mel_normalize=True for [-1,1] power normalization)
    net_t=UNetV0, # The model type used for diffusion vocoding
    channels=[8, 32, 64, 128, 256, 512, 512, 1024, 1024], # U-Net: channels at each layer
    factors=[1, 4, 4, 4, 2, 2, 2, 2, 2], # U-Net: downsampling and upsampling factors at each layer
    items=[1, 2, 2, 2, 2, 2, 2, 4, 4], # U-Net: number of repeating items at each layer
    diffusion_t=VDiffusion, # The diffusion method used
    sampler_t=VSampler, # The diffusion sampler used
)

# Train model on waveforms (automatically converted to mel internally)
audio = torch.randn(1, 2, 2**18) # [batch, in_channels, length]
loss = vocoder(audio)
loss.backward()

# Turn mel spectrogram into waveform
mel_spectrogram = torch.randn(1, 2, 80, 1024) # [batch, in_channels, mel_channels, mel_length]
sample = vocoder.sample(mel_spectrogram, num_steps=10) # Output has shape: [1, 2, 2**18]

In [15]:
from IPython.display import Audio
import torch

# Assuming your tensor is named 'audio_tensor'
# Convert the tensor to a NumPy array
audio_array = sample.numpy().reshape(-1)

# Specify the sample rate (replace with your actual sample rate)
sample_rate = 44100

# Use the Audio class to play the audio in Colab
Audio(data=audio_array, rate=sample_rate)